In [1]:
import pandas as pd
from sqlalchemy import create_engine

Database connection

In [13]:
pw = "password1999"
connection_string = 'mysql+pymysql://root:' + pw + '@localhost:3306/'
engine = create_engine(connection_string, pool_pre_ping = False)

### Reshape tables

In [14]:
dataset_codes = ['sdg_01_10', 'sdg_01_10a', 'sdg_01_20', 'sdg_01_20a', 'sdg_01_31', 'sdg_01_40', 'sdg_01_41', 'sdg_01_50', 'sdg_03_60', 'sdg_10_30', 'sdg_11_11', 'sdg_02_10', 'sdg_02_20', 'sdg_02_30', 'sdg_02_40', 'sdg_02_60', 'sdg_06_40', 'sdg_15_50', 'sdg_15_60', 'sdg_03_11', 'sdg_03_20', 'sdg_03_30', 'sdg_03_41', 'sdg_03_42', 'sdg_08_60', 'sdg_11_20', 'sdg_11_40', 'sdg_11_52', 'sdg_04_10', 'sdg_04_10a', 'sdg_04_20', 'sdg_04_31', 'sdg_04_40', 'sdg_04_60', 'sdg_04_70', 'sdg_05_10', 'sdg_05_20', 'sdg_05_30', 'sdg_05_40', 'sdg_05_50', 'sdg_05_60', 'sdg_06_10', 'sdg_06_20', 'sdg_06_30', 'sdg_06_50', 'sdg_06_60', 'sdg_14_40', 'sdg_07_10', 'sdg_07_11', 'sdg_07_20', 'sdg_07_30', 'sdg_07_40', 'sdg_07_50', 'sdg_07_60', 'sdg_08_10', 'sdg_08_11', 'sdg_08_20', 'sdg_08_20a', 'sdg_08_30', 'sdg_08_30a', 'sdg_08_40', 'sdg_12_21', 'sdg_09_10', 'sdg_09_30', 'sdg_09_40', 'sdg_09_50', 'sdg_09_60', 'sdg_09_70', 'sdg_12_61', 'sdg_17_60', 'sdg_10_10', 'sdg_10_20', 'sdg_10_41', 'sdg_10_50', 'sdg_10_60', 'sdg_11_31', 'sdg_11_60', 'sdg_16_20', 'sdg_12_10', 'sdg_12_30', 'sdg_12_41', 'sdg_12_51', 'sdg_13_10', 'sdg_13_21', 'sdg_13_40', 'sdg_13_50', 'sdg_13_60', 'sdg_14_10', 'sdg_14_21', 'sdg_14_30', 'sdg_14_50', 'sdg_14_60', 'sdg_15_10', 'sdg_15_20', 'sdg_15_41', 'sdg_15_61', 'sdg_16_10', 'sdg_16_30', 'sdg_16_40', 'sdg_16_50', 'sdg_16_60', 'sdg_17_10', 'sdg_17_20', 'sdg_17_30', 'sdg_17_40', 'sdg_17_50', 'sdg_02_52', 'sdg_11_51', 'sdg_12_50', 'sdg_01_30', 'sdg_01_60', 'sdg_02_51', 'sdg_11_10', 'sdg_11_50', 'sdg_12_20', 'sdg_13_20', 'sdg_13_30', 'sdg_03_10', 'sdg_04_30', 'sdg_04_50', 'sdg_09_21', 'sdg_02_50', 'sdg_03_40', 'sdg_09_20', 'sdg_12_60']

In [15]:
def split_years_non_years(columns_name) :
    years_list = []
    non_years_list =[]
    for column_name in columns_name :
        try :
            years_list.append(int(column_name))
        except :
            non_years_list.append(column_name)
    
    return (years_list,non_years_list)

In [30]:
for dataset_code in dataset_codes :
    sql = f""" 
    SELECT *
    FROM eurostat.{dataset_code}
    """
    dataset = pd.read_sql(sql, engine)
    dataset.set_index(split_years_non_years(dataset.columns)[1], inplace= True) #Set all columns as index except years
    dataset = dataset.stack() #Set years as rows
    dataset = dataset.reset_index()
    dataset.columns = list(dataset.columns)[:-2]+ ["Years","KPI"] #Set correct columns names
    dataset.to_sql(dataset_code, connection_string, schema="eurostat", if_exists='replace', index = False)

### Rename country code with full names

In [31]:
country_codes_to_names = {
    'BE': 'Belgium',
    'EL': 'Greece',
    'LT': 'Lithuania',
    'PT': 'Portugal',
    'BG': 'Bulgaria',
    'ES': 'Spain',
    'LU': 'Luxembourg',
    'RO': 'Romania',
    'CZ': 'Czechia',
    'FR': 'France',
    'HU': 'Hungary',
    'SI': 'Slovenia',
    'DK': 'Denmark',
    'HR': 'Croatia',
    'MT': 'Malta',
    'SK': 'Slovakia',
    'DE': 'Germany',
    'IT': 'Italy',
    'NL': 'Netherlands',
    'FI': 'Finland',
    'EE': 'Estonia',
    'CY': 'Cyprus',
    'AT': 'Austria',
    'SE': 'Sweden',
    'IE': 'Ireland',
    'LV': 'Latvia',
    'PL': 'Poland',
    'MK': 'North Macedonia',
    'UK': 'United Kingdom',
    'NO': 'Norway',
    'TR': 'Türkiye',
    'CH': 'Switzerland',
    'IS': 'Iceland',
    'RS': 'Serbia',
    'ME': 'Montenegro',
    'AL': 'Albania'
}

In [32]:
def replace_country_name(df) :
    new_country_names = [] 
    for country_name in df['geo\\TIME_PERIOD'] :
        if country_name in country_codes_to_names.keys() :
            new_country_names.append(country_codes_to_names[country_name])
        else :
            new_country_names.append(country_name)
            print(country_name, "don't matche")
    return new_country_names

In [33]:
for dataset_code in dataset_codes :
    sql = f""" 
    SELECT *
    FROM eurostat.{dataset_code}
    """
    dataset = pd.read_sql(sql, engine)
    try : 
        dataset["geo\\TIME_PERIOD"]=replace_country_name(dataset) #Replace contry codes with full names
    except : 
        print(dataset_code)
    dataset.to_sql(dataset_code, connection_string, schema="eurostat", if_exists='replace', index = False)

Albania don't matche
Albania don't matche
Albania don't matche
Albania don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Czechia don't matche
Czechia don't matche
Cz

In [34]:
df = pd.read_sql("SELECT * FROM eurostat.sdg_01_10", con  = connection_string)
df.head()

freq sex    age unit geo\TIME_PERIOD Years   KPI
0    A   T  TOTAL   PC         Albania  2017  58.5
1    A   T  TOTAL   PC         Albania  2018  53.9
2    A   T  TOTAL   PC         Albania  2019  50.7
3    A   T  TOTAL   PC         Albania  2020  46.2
4    A   T  TOTAL   PC         Austria  2015  16.9

In [35]:
df["geo\\TIME_PERIOD"]=replace_country_name(df)

Albania don't matche
Albania don't matche
Albania don't matche
Albania don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Austria don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Belgium don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Bulgaria don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Switzerland don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Cyprus don't matche
Czechia don't matche
Czechia don't matche
Cz

In [36]:
df

freq sex     age     unit geo\TIME_PERIOD Years      KPI
0       A   T   TOTAL       PC         Albania  2017     58.5
1       A   T   TOTAL       PC         Albania  2018     53.9
2       A   T   TOTAL       PC         Albania  2019     50.7
3       A   T   TOTAL       PC         Albania  2020     46.2
4       A   T   TOTAL       PC         Austria  2015     16.9
...   ...  ..     ...      ...             ...   ...      ...
1211    A   T  Y_LT18  THS_PER         Türkiye  2021  10307.0
1212    A   T  Y_LT18  THS_PER  United Kingdom  2015   3952.0
1213    A   T  Y_LT18  THS_PER  United Kingdom  2016   3649.0
1214    A   T  Y_LT18  THS_PER  United Kingdom  2017   3861.0
1215    A   T  Y_LT18  THS_PER  United Kingdom  2018   4021.0

[1216 rows x 7 columns]

Créer une colonne pour les demandeurs d'adhésion